In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load in 

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the "../input/" directory.
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os


# Any results you write to the current directory are saved as output.

In [2]:
import numpy as np
import pandas as pd
import os
import json
import glob
import sys

sys.path.insert(0, "../")

root_path = '/kaggle/input/CORD-19-research-challenge/2020-03-13'

corona_features = {"doc_id": [None], "source": [None], "title": [None],
                  "abstract": [None], "text_body": [None]}
corona_df = pd.DataFrame.from_dict(corona_features)

json_filenames = glob.glob(f'{root_path}/**/*.json', recursive=True)

In [3]:
def return_corona_df(json_filenames, df, source):

    for file_name in json_filenames:

        row = {"doc_id": None, "source": None, "title": None,
              "abstract": None, "text_body": None}

        with open(file_name) as json_data:
            data = json.load(json_data)

            doc_id = data['paper_id']
            row['doc_id'] = doc_id
            row['title'] = data['metadata']['title']

            # Now need all of abstract. Put it all in 
            # a list then use str.join() to split it
            # into paragraphs. 

            abstract_list = [abst['text'] for abst in data['abstract']]
            abstract = "\n ".join(abstract_list)

            row['abstract'] = abstract

            # And lastly the body of the text. 
            body_list = [bt['text'] for bt in data['body_text']]
            body = "\n ".join(body_list)
            
            row['text_body'] = body
            
            # Now just add to the dataframe. 
            
            if source == 'b':
                row['source'] = "BIORXIV"
            elif source == "c":
                row['source'] = "COMMON_USE_SUB"
            elif source == "n":
                row['source'] = "NON_COMMON_USE"
            elif source == "p":
                row['source'] = "PMC_CUSTOM_LICENSE"
            
            df = df.append(row, ignore_index=True)
    
    return df
    
corona_df = return_corona_df(json_filenames, corona_df, 'b')


In [4]:
corona_out = corona_df.to_csv('kaggle_covid-19_open_csv_format.csv')

In [5]:
corona_df = corona_df.dropna()

In [6]:
from IPython.display import FileLink
FileLink(r'kaggle_covid-19_open_csv_format.csv')

/kaggle/working/kaggle_covid-19_open_csv_format.csv

In [7]:
!pip install ktrain

     |████████████████████████████████| 25.2 MB 7.5 MB/s 
     |████████████████████████████████| 6.7 MB 41.9 MB/s 
     |████████████████████████████████| 10.1 MB 57.5 MB/s 
     |████████████████████████████████| 241 kB 41.6 MB/s 
     |████████████████████████████████| 1.7 MB 39.0 MB/s 
     |████████████████████████████████| 3.1 MB 30.7 MB/s 
  Created wheel for ktrain: filename=ktrain-0.11.0-py3-none-any.whl size=25213643 sha256=8274d8548df8498a4d79334ed4dabfd7addc1c29621ce81cb362a8b897a364bc
  Stored in directory: /root/.cache/pip/wheels/ff/35/92/ac63fa6a03754ce583c180eb8c17bfe8e73c6c513855597ead
  Created wheel for keras-bert: filename=keras_bert-0.81.0-py3-none-any.whl size=37912 sha256=212fc564d3b6ee768c2a4f064b037e88ce04ef078f585454b7e1499125124fe6
  Stored in directory: /root/.cache/pip/wheels/ee/d9/2a/75b40df359ab9096f06e55804ca64fbb2592a6ff77345c5fa7
  Created wheel for networkx: filename=networkx-2.3-py2.py3-none-any.whl size=1556408 sha256=20763bca1aec13620014510a3bfb2dd

In [8]:
import ktrain
ktrain.text.preprocessor.detect_lang = ktrain.text.textutils.detect_lang
df = corona_df
texts = df["text_body"]
tm = ktrain.text.get_topic_model(texts, n_topics=None, n_features=10000)

n_topics automatically set to 81
lang: en
preprocessing texts...
fitting model...
iteration: 1 of max_iter: 5
iteration: 2 of max_iter: 5
iteration: 3 of max_iter: 5
iteration: 4 of max_iter: 5
iteration: 5 of max_iter: 5
done.


In [9]:
tm.print_topics()
tm.build(texts, threshold=0.25)

topic 0 | insulin glucose pca fgl2 degs pbm cd13 liver sham tev
topic 1 | species bats bat hev humans host hosts reservoir niv zoonotic
topic 2 | sirna target mirnas sirnas knockdown mirna gene expression rna rnai
topic 3 | patients mortality sepsis blood plasma mean serum ards hours cardiac
topic 4 | lasv pools pool aiv sftsv zone fever ticks lbms tick
topic 5 | membrane proteins fusion hcv hiv-1 entry virions particles golgi cellular
topic 6 | mers-cov mers camels rbd saudi camel dpp4 arabia middle east
topic 7 | expression pathway activation signaling apoptosis pathways stress phosphorylation activity involved
topic 8 | brain cns encephalitis neurological htlv-1 neurotropic tax ltr unigenes ly-6c
topic 9 | a1111111111 iran health-care triage rca wgs arab israel uae emr
topic 10 | particles vlps capsid vlp norovirus gii vp1 baculovirus insect recombinant
topic 11 | doi preprint https org/10 peer-reviewed copyright holder author/funder biorxiv allowed
topic 12 | sars-cov sars coronavi

In [10]:
texts = tm.filter(texts)
df = tm.filter(df)

In [11]:
tm.visualize_documents(doc_topics=tm.get_doctopics())

reducing to 2 dimensions...[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 11102 samples in 0.032s...
[t-SNE] Computed neighbors for 11102 samples in 17.078s...
[t-SNE] Computed conditional probabilities for sample 1000 / 11102
[t-SNE] Computed conditional probabilities for sample 2000 / 11102
[t-SNE] Computed conditional probabilities for sample 3000 / 11102
[t-SNE] Computed conditional probabilities for sample 4000 / 11102
[t-SNE] Computed conditional probabilities for sample 5000 / 11102
[t-SNE] Computed conditional probabilities for sample 6000 / 11102
[t-SNE] Computed conditional probabilities for sample 7000 / 11102
[t-SNE] Computed conditional probabilities for sample 8000 / 11102
[t-SNE] Computed conditional probabilities for sample 9000 / 11102
[t-SNE] Computed conditional probabilities for sample 10000 / 11102
[t-SNE] Computed conditional probabilities for sample 11000 / 11102
[t-SNE] Computed conditional probabilities for sample 11102 / 11102
[t-SNE] Mean sigma: 0.

Loading BokehJS ...

> What is known about transmission, incubation, and environmental stability?
* 

In [12]:
transmission_results = tm.search('transmission', case_sensitive=False)
incubation_results = tm.search('incubation', case_sensitive=False)
environmental_results = tm.search('environmental stability', case_sensitive=False)

In [13]:
threshold = .80

transmission_topic_ids = {doc[3] for doc in transmission_results if doc[2]>threshold}
incubation_topic_ids = {doc[3] for doc in incubation_results if doc[2]>threshold}
environmental_topic_ids = {doc[3] for doc in environmental_results if doc[2]>threshold}

t_topics = transmission_topic_ids.copy()
t_topics.update(incubation_topic_ids)
t_topics.update(environmental_topic_ids)


In [14]:

tm.visualize_documents(doc_topics=tm.get_doctopics(t_topics))


reducing to 2 dimensions...[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 4552 samples in 0.011s...
[t-SNE] Computed neighbors for 4552 samples in 2.143s...
[t-SNE] Computed conditional probabilities for sample 1000 / 4552
[t-SNE] Computed conditional probabilities for sample 2000 / 4552
[t-SNE] Computed conditional probabilities for sample 3000 / 4552
[t-SNE] Computed conditional probabilities for sample 4000 / 4552
[t-SNE] Computed conditional probabilities for sample 4552 / 4552
[t-SNE] Mean sigma: 0.102189
[t-SNE] KL divergence after 250 iterations with early exaggeration: 68.127075
[t-SNE] KL divergence after 1000 iterations: 1.095905
done.


Loading BokehJS ...

In [15]:
docs = tm.get_docs(topic_ids=t_topics, rank=True)
print("TOTAL_NUM_OF_DOCS: %s" % len(docs))

print("##################################")

for t in t_topics:
    docs = tm.get_docs(topic_ids=[t], rank=True)
    print("NUM_OF_DOCS: %s" % len(docs))
    if(len(docs)==0): continue
    doc = docs[1]
    print('TOPIC_ID: %s' % (doc[3]))
    print('TOPIC: %s' % (tm.topics[t]))
    print('DOC_ID: %s'  % (doc[1]))
    print('TOPIC SCORE: %s '% (doc[2]))
    print('TEXT: %s' % (doc[0][0:400]))
    
    
    print("##################################")


TOTAL_NUM_OF_DOCS: 4552
##################################
NUM_OF_DOCS: 263
TOPIC_ID: 64
TOPIC: public people social work policy media risk government need issues
DOC_ID: 694
TOPIC SCORE: 0.7814177363397491 
TEXT: Dr. Carlo Urbani was the first person to recognize Severe Acute Respiratory Syndrome (SARS) in a Hanoi, Vietnam, hospital. On March 29, 2003, only one month after the discovery, Dr. Urbani died from the disease, largely because of his belief that it is a doctor's duty to "stay close to the victims." His wife, Giuliani, mother of three, challenged her husband on the point; Dr. Urbani replied, "If I
##################################
NUM_OF_DOCS: 217
TOPIC_ID: 3
TOPIC: patients mortality sepsis blood plasma mean serum ards hours cardiac
DOC_ID: 300
TOPIC SCORE: 0.8617904292419983 
TEXT: Sepsis and septic shock are medical emergencies for which treatment and resuscitation should begin immediately. The goals of fluid resuscitation for these patients are: a) to rapidly replace int

In [16]:
tm.train_recommender()


In [17]:
text = "What is known about covid-19 transmission?"
for i, doc in enumerate(tm.recommend(text=text, n=5)):
    print('RESULT #%s'% (i+1))
    print('TEXT:\n\t%s' % (" ".join(doc[0].split()[:500])))
    print()

RESULT #1
TEXT:
	Influenza, commonly known as the flu, is a severe infectious disease accounting for between 250 000 and 500 000 deaths worldwide every year. Millions of people died in the influenza pandemic of 1918, one of the worst epidemic disasters in recorded human history. 1 The life style of modern society, including overcrowded cities and rapid global transportation, has resulted in dissemination of influenza and generation of novel virus strains. In the past year, the World Health Organization (WHO) announced a level-6 alert for the influenza A (H1N1) pandemic, the highest level of disease outbreak, because of the sustained spread of this new virus on a global scale. 2 The world was fortunate not to have experienced another devastating influenza epidemic, because the fatality rate of the new virus strain was similar to seasonal influenza virus. 3 However, there remains an inevitability of a new influenza pandemic, which could be highly infectious and as deadly as the 1918 infl

In [18]:
text = "What is known about covid-19 incubation period?"
for i, doc in enumerate(tm.recommend(text=text, n=5)):
    print('RESULT #%s'% (i+1))
    print('TEXT:\n\t%s' % (doc[0]))
    print()

RESULT #1
TEXT:
	Influenza, commonly known as the flu, is a severe infectious disease accounting for between 250 000 and 500 000 deaths worldwide every year. Millions of people died in the influenza pandemic of 1918, one of the worst epidemic disasters in recorded human history. 1 The life style of modern society, including overcrowded cities and rapid global transportation, has resulted in dissemination of influenza and generation of novel virus strains. In the past year, the World Health Organization (WHO) announced a level-6 alert for the influenza A (H1N1) pandemic, the highest level of disease outbreak, because of the sustained spread of this new virus on a global scale. 2 The world was fortunate not to have experienced another devastating influenza epidemic, because the fatality rate of the new virus strain was similar to seasonal influenza virus. 3 However, there remains an inevitability of a new influenza pandemic, which could be highly infectious and as deadly as the 1918 infl

In [19]:
text = "What is known about covid-19 environmental stability?"
for i, doc in enumerate(tm.recommend(text=text, n=5)):
    print('RESULT #%s'% (i+1))
    print('TEXT:\n\t%s' % (doc[0]))
    print()

RESULT #1
TEXT:
	H uman subcutaneous dirofilariasis (HSD) is a zoonotic filariasis caused by infection with several species of worms belonging to the genus Dirofilaria; most documented cases are attributed to Dirofilaria repens (1) . Dirofilarias are natural parasites of a great variety of animals and, with the exception of D. immitis, live in the subcutaneous tissue of their hosts, produce circulating microfilariae, and are transmitted by mosquitoes (2) . The principal reservoir of D. repens is the dog. Humans are accidental hosts with patent infections being extremely rare. Differential diagnoses of HSD include neoplasia and other granulomatous diseases, and a definitive diagnosis usually requires surgical removal and examination of a granuloma.
 Current epidemiologic studies indicate that human dirofilariasis is increasing in prevalence, and several authors have recently described it as an emerging disease in different areas of the world. Pampiglione et al. (3) reported 60 new cases